In [0]:
%pip install mlflow
%load_ext autoreload
%autoreload 2

Python interpreter will be restarted.
Requirement already satisfied: mlflow in /databricks/python3/lib/python3.8/site-packages (2.2.2)
Requirement already satisfied: scipy<2 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.6.2)
Requirement already satisfied: requests<3,>=2.17.3 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2.32.3)
Requirement already satisfied: entrypoints<1 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.3)
Requirement already satisfied: markdown<4,>=3.3 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.7)
Requirement already satisfied: cloudpickle<3 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2.2.1)
Requirement already satisfied: scikit-learn<2 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.0.2)
Requirement already satisfied: shap<1,>=0.40 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.44.1)
Requirement already satisfied: pytz<2023 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2020.5)
Requirement already satisfied: pyyaml<7,>=5.1 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (6.0.2)
Requirement already satisfied: docker<7,>=4.0.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (6.1.3)
Requirement already satisfied: pandas<3 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.4.4)
Requirement already satisfied: querystring-parser<2 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.2.4)
Requirement already satisfied: numpy<2 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.22.4)
Requirement already satisfied: importlib-metadata!=4.7.0,<7,>=3.7.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (6.11.0)
Requirement already satisfied: protobuf<5,>=3.12.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.17.2)
Requirement already satisfied: pyarrow<12,>=4.0.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (4.0.0)
Requirement already satisfied: Flask<3 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2.3.3)
Requirement already satisfied: packaging<24 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (23.2)
Requirement already satisfied: databricks-cli<1,>=0.8.7 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.18.0)
Requirement already satisfied: alembic<2 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.13.3)
Requirement already satisfied: sqlparse<1,>=0.4.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.5.1)
Requirement already satisfied: matplotlib<4 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.4.2)
Requirement already satisfied: gunicorn<21 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (20.1.0)
Requirement already satisfied: Jinja2<4,>=2.11 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.1.4)
Requirement already satisfied: gitpython<4,>=2.1.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.1.43)
Requirement already satisfied: click<9,>=7.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (8.1.7)
Requirement already satisfied: sqlalchemy<3,>=1.4.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2.0.35)
Requirement already satisfied: importlib-resources in /databricks/python3/lib/python3.8/site-packages (from alembic<2->mlflow) (6.4.5)
Requirement already satisfied: typing-extensions>=4 in /databricks/python3/lib/python3.8/site-packages (from alembic<2->mlflow) (4.12.2)
Requirement already satisfied: Mako in /databricks/python3/lib/python3.8/site-packages (from alembic<2->mlflow) (1.3.5)
Requirement already satisfied: oauthlib>=3.1.0 in /databricks/python3/lib/python3.8/site-packages (from databricks-cli<1,>=0.8.7->mlflow) (3.2.2)
Requirement already satisfied: pyjwt>=1.7.0 in /databricks/python3/lib/python3.8/sit

In [0]:
dbutils.widgets.dropdown("env_stage", "dev", ["dev", "prod"], "Pipeline stage")
dbutils.widgets.dropdown("exclude_pms", "False", ["True", "False"], "Exclude PMS")
dbutils.widgets.dropdown("target_type", "REVENUE", ["REVENUE", "ROOMS"], "Target Type")
dbutils.widgets.dropdown("is_usd_currency", "True", ["True", "False"], "Use USD currency")
dbutils.widgets.text("selected_hotels", "", "Hotels")
dbutils.widgets.text("lag_numbers","1,7,14,28", "Lag Numbers")

In [0]:
import pandas as pd
import numpy as np
from pyspark.sql.functions import *
from pyspark.sql.types import *
from typing import List
import holidays
import matplotlib
import seaborn as sns
from datetime import datetime, timezone
from pathlib import Path
import pickle
import os
from sys import version_info
import cloudpickle
from autogluon.core.utils.loaders import load_pkl
import logging
import shutil
import mlflow
from mlflow import MlflowException
import mlflow.pyfunc
import time
import warnings

warnings.filterwarnings("ignore")
start_time = time.perf_counter()

In [0]:
ENV = getArgument("env_stage")

REPOPATH = "/Workspace/Repos/manik@surge.global/phg-data-mlsys/src"
cluster_name = spark.conf.get("spark.databricks.clusterUsageTags.clusterName") 

if (ENV == "dev") and ("dev" in cluster_name):
    print(f"Loading phgml package from repo {REPOPATH}")
    sys.path.append(os.path.abspath(REPOPATH))

In [0]:
from phgml.data.processing_distr_ca import filter_hotels, filter_test_partition
from phgml.data.processing_distr_spark import (
    preprocess_data,
    calc_date_features,
    get_lags,
    compile_hotel_tables,
)
from phgml.reporting.output_metrics import *
from phgml.data.data_types import inference_output_schema
from phgml.reporting.logging import get_dbx_logger
from phgml.data.config import ForecastingHotelConfigProvider,EnvironmentConfig

In [0]:
def str_to_lst(value):
    if value == "":
        return []
    elif "," in value:
        hotels = value.split(",")
        return hotels

    return [value]

def str_to_bool(value):
    FALSE_VALUES = ["false", "no", "0"]
    TRUE_VALUES = ["true", "yes", "1"]
    lvalue = str(value).lower()
    if lvalue in (FALSE_VALUES):
        return False
    if lvalue in (TRUE_VALUES):
        return True
    raise Exception(
        "String value should be one of {}, but got '{}'.".format(
            FALSE_VALUES + TRUE_VALUES, value
        )
    )

# Disable adaptive query optimization
# Adaptive query optimization groups together smaller tasks into a larger tasks.
# This may result in limited parallelism if the parallel inference tasks are deemed to be too small by the query optimizer
# We are diableing AQE here to circumevent this limitation on parallelism
spark.conf.set("spark.sql.adaptive.enabled", "false")

In [0]:
REVENUE_COL = "_reservationRevenuePerRoomUSD"
ROOMS_COL = "_rooms"
PIPELINE = "INFERENCE"

WITHOUT_PMS = str_to_bool(getArgument("exclude_pms"))
IS_USD_CURRENCY = str_to_bool(getArgument("is_usd_currency"))
TARGET_TYPE = getArgument("target_type")
selected_hotels = str_to_lst(getArgument("selected_hotels"))
LAG_NUMBERS = list(map(int,str_to_lst(getArgument('lag_numbers'))))

### The start of the model data
MODEL_START_DATE = pd.to_datetime("2018-10-01")

COVID_START_DATE = pd.to_datetime("2020-03-01")
COVID_END_DATE = pd.to_datetime("2021-08-01")

CALC_UNCERTAINTY = False
# MODEL_TYPE = "XGB"  # Use "AG" to try out the auto gloun approach
MODEL_TYPE = "AG"

ML_EXPERIMENT_ID = 1079527465953184

if MODEL_TYPE == "XGB":
    RUN_ID = "92907cac187f4c8cadb63ff60a05d72e"  # XGB Run
elif CALC_UNCERTAINTY and (MODEL_TYPE == "AG"):
    RUN_ID = "9549361574484dc58fcf1b7d130541a0"
else:
    RUN_ID = "19dee6420aed45f29e956016c5ea6e8a"


In [0]:
env_config = EnvironmentConfig(env=ENV, target=TARGET_TYPE, spark=spark, is_usd_currency=IS_USD_CURRENCY)
forecasting_config_provider = ForecastingHotelConfigProvider(spark=spark,env=ENV)
target_column = env_config.target_column
schema = inference_output_schema

In [0]:
hotel_ids = spark.sql(
    f"select distinct HotelID,HotelName from {env_config.source_data_table}"
).toPandas()
hotel_ids = hotel_ids.sort_values("HotelID")

In [0]:
# As a workaround for the bug PHG-2157
PARTITION_DATE = spark.sql(
    f"select max(confirmationDate) from {env_config.source_data_table}"
).collect()[0][0]

print(PARTITION_DATE)

2024-10-07

In [0]:
max_inference_length = spark.sql(f'select max(inference_prediction_length) from {forecasting_config_provider.config_table_name}').collect()[0][0]
max_lead_window = spark.sql(f'select max(lead_window) from {forecasting_config_provider.config_table_name}').collect()[0][0]
TEST_PARTIITON_END = PARTITION_DATE + pd.Timedelta(max_inference_length, "D")

In [0]:
TEST_PARTIITON_END,PARTITION_DATE

Out[11]: (datetime.date(2024, 11, 4), datetime.date(2024, 10, 7))

In [0]:
logger = get_dbx_logger(pipeline=PIPELINE,
                        task_type=TARGET_TYPE,
                        exclude_pms=WITHOUT_PMS)
logger.setLevel(logging.INFO)

In [0]:
env_config.inference_output_table = "test_inference_preprocessed_data"
env_config.inference_intermediate_table = "test_inference_intermediate_data"
print(f"Executing pipeline stage: {ENV}")
print(f"Processing data for target type: {TARGET_TYPE} : {target_column}")
print(f"Intermediate inference results table name: {env_config.inference_intermediate_table }")
print(f"Writing inference results to table: {env_config.inference_output_table } with blob {env_config.inference_output_table_blob}")
print(f"Excluding PMS data? {WITHOUT_PMS}")

Executing pipeline stage: dev
Processing data for target type: REVENUE : _reservationRevenuePerRoomUSD
Intermediate inference results table name: test_inference_intermediate_data
Writing inference results to table: test_inference_preprocessed_data with blob /mnt/transformation/synxis/dev_forecast_revenue
Excluding PMS data? False

In [0]:
logger.info(f"Executing pipeline stage: {ENV}")
logger.info(f"Processing data for target type: {TARGET_TYPE} : {target_column}")
logger.info(f"Intermediate inference results table name: {env_config.inference_intermediate_table }")
logger.info(f"Writing inference results to table: {env_config.inference_output_table } with blob {env_config.inference_output_table_blob}")
logger.info(f"Excluding PMS data? {WITHOUT_PMS}")

24/10/08/ 05:06:55 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Executing pipeline stage: dev
Executing pipeline stage: dev
24/10/08/ 05:06:55 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Processing data for target type: REVENUE : _reservationRevenuePerRoomUSD
Processing data for target type: REVENUE : _reservationRevenuePerRoomUSD
24/10/08/ 05:06:55 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Intermediate inference results table name: test_inference_intermediate_data
Intermediate inference results table name: test_inference_intermediate_data
24/10/08/ 05:06:55 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Writing inference results to table: test_inference_preprocessed_data with blob /mnt/transformation/synxis/dev_forecast_revenue
Writing inference results to table: test_inference_preprocessed_data with blob /mnt/transformation/synxis/dev_forecast_revenue
24/10/08/ 05:06:55 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Excluding PMS data? False
Excluding PMS data? False

In [0]:
logger.info("Selecting hotels.")

hotel_details = spark.sql(
    "select HotelID,HotelName,PMSStartDate from phg_data.dim_hotels_"
).toPandas()

#ADHOC CHANGE
# since some pms hotels has only recent pms data, need to temporarily filter them out
# to avoid the inference pipeline failure
if not WITHOUT_PMS:
    hotel_details['PMSStartDate'] = pd.to_datetime(hotel_details['PMSStartDate'] )
    min_past_date= pd.to_datetime('2024-05-01')-pd.to_timedelta(365, unit='days')
    hotel_details = hotel_details[(hotel_details['PMSStartDate'] <= min_past_date)|(hotel_details['PMSStartDate'].isna())] 

#Filter hotels 
correct_hotel_ids = filter_hotels(hotel_details,selected_hotels,WITHOUT_PMS,forecasting_config_provider)

24/10/08/ 05:06:55 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Selecting hotels.
Selecting hotels.

In [0]:
columns = [
    "HotelID",
    "_StayDates",
    "confirmationDate",
    "departureDate",
    "channel",
    "status",
    REVENUE_COL,
    ROOMS_COL,
]
dfsp = spark.sql(
    f"select {','.join(columns)} from {env_config.source_data_table} where status='Confirmed'"
)

if correct_hotel_ids:
    print(f"Filtering data for the selected hotels: {correct_hotel_ids}")
    dfsp = dfsp.filter(dfsp.HotelID.isin(correct_hotel_ids))

Filtering data for the selected hotels: ['7131', '35138', '1406', '79051', '60302', '27003', '26855', '63717', '7824', '32498', '31122', '60457', '70214', '39664', '51829', '27055', '59104', '29883', '67543', '55810', '26834', '35332', '77854', '71999', '35653', '59968', '10443', '64688', '7132', '27286', '26830', '56217', '27172', '36063', '64942', '76630', '2002', '27226', '75045', '53654', '9718', '27213', '63662']

In [0]:
logger.info("Preprocessing data")
df = preprocess_data(
    dfsp,
    WITHOUT_PMS,
    REVENUE_COL,
    ROOMS_COL,
    MODEL_START_DATE,
    cancel_aware=False,
).orderBy(["HotelID", "_StayDates","confirmationDate"])

logger.info("Calculating date features")
dates = spark.createDataFrame(calc_date_features(df).reset_index().rename(columns={"index":"_StayDates"}))

logger.info("Calculating lag features")
df_lags = get_lags(df,lag_numbers=LAG_NUMBERS, target_col=target_column)


logger.info("Filtering test partition")
df = filter_test_partition(
    df=df,
    partition_start=PARTITION_DATE,
    partition_end=TEST_PARTIITON_END,
    revenue_col=REVENUE_COL,
    rooms_col=ROOMS_COL,
    cancel_aware=False
).orderBy(["HotelID", "_StayDates","confirmationDate"])

24/10/08/ 05:06:56 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Preprocessing data
Preprocessing data
cancel_aware : False
24/10/08/ 05:06:56 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Calculating date features
Calculating date features
24/10/08/ 05:07:40 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Calculating lag features
Calculating lag features
24/10/08/ 05:07:40 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Filtering test partition
Filtering test partition

In [0]:
logger.info("Compiling test data set")
output_df = compile_hotel_tables(
    df=df,
    target_type=TARGET_TYPE,
    target_column=target_column,
    prediction_horizon=max_inference_length,
    lead_window=max_lead_window,
    selected_hotels=correct_hotel_ids,
    dates=dates,
    df_lags=df_lags,
    spark=spark,
    cancel_aware=False,
    suffix=""
).orderBy(["HotelID", "_StayDates"])

24/10/08/ 05:07:40 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Compiling test data set
Compiling test data set

In [0]:
env_config.preprocess_intermediate_table = "test_preprocess_intermediate_table"

In [0]:
# logger.info("Drop intermediate preprocess table if it exists")
# spark.sql(f"DROP TABLE IF EXISTS {env_config.preprocess_intermediate_table}")

In [0]:
logger.info(
    f"Writing preprocess data to temporary table {env_config.preprocess_intermediate_table}"
)
(
    output_df.write.mode("overwrite")
    .option("overwriteSchema", "true")
    .saveAsTable(env_config.preprocess_intermediate_table)
)

24/10/08/ 05:07:42 UTC:PHGML-INFERENCE-REVENUE-PMS-INFO-Writing preprocess data to temporary table test_preprocess_intermediate_table
Writing preprocess data to temporary table test_preprocess_intermediate_table

In [0]:
%sql
select count(HotelID) from test_preprocess_intermediate_table

_StayDates HotelID RV0 RV1 RV2 RV3 RV4 RV5 RV6 RV7 RV8 RV9 RV10 RV11 RV12 RV13 RV14 RV15 RV16 RV17 RV18 RV19 RV20 RV21 RV22 RV23 RV24 RV25 RV26 RV27 RV28 RV29 RV30 RV31 RV32 RV33 RV34 RV35 RV36 RV37 RV38 RV39 RV40 RV41 RV42 RV43 RV44 RV45 RV46 RV47 RV48 RV49 RV50 RV51 RV52 RV53 RV54 RV55 RV56 RV57 RV58 RV59 RV60 RV61 RV62 RV63 RV64 RV65 RV66 RV67 RV68 RV69 RV70 RV71 RV72 RV73 RV74 RV75 RV76 RV77 RV78 RV79 RV80 RV81 RV82 RV83 RV84 RV85 RV86 RV87 RV88 RV89 RV90 RV91 RV92 RV93 RV94 RV95 RV96 RV97 RV98 RV99 year quarter_of_year month_of_year week_of_year day_of_year month_of_quarter week_of_quarter day_of_quarter week_of_month day_of_month holiday day_of_week_0 day_of_week_1 day_of_week_2 day_of_week_3 day_of_week_4 day_of_week_5 day_of_week_6 lag1 lag7 lag14 lag28 2024-10-12 31122 157344.37000000002 157344.37000000002 157344.37000000002 157344.37000000002 157344.37000000002 157344.37000000002 157344.37000000002 157344.37000000002 155557.37000000002 155557.37000000002 154862.37000000002 151166.87000000002 150341.87000000002 150341.87000000002 147257.37000000002 147257.37000000002 145312.37000000002 145312.37000000002 145312.37000000002 143422.37000000002 139743.7 139743.7 139743.7 138086.7 132441.94 132441.94 129680.27 128200.77 125204.77 122431.66 122431.66 122431.66 92555.41 92555.41 92555.41 89394.91 89394.91 85221.41 85221.41 85221.41 85221.41 85221.41 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 82059.06 78978.73 78183.73 78183.73 76853.73 76853.73 76853.73 75775.43 75775.43 75775.43 75775.43 74385.43 74385.43 66435.43 66435.43 64625.43 64625.43 64625.43 64625.43 64625.43 64625.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 62958.43 60933.43 60933.43 60933.43 60933.43 60933.43 60933.43 60933.43 2024 4 10 41 286 3 2 12 2 12 0 0 0 0 0 0 1 0 164956.3 184656.95999999996 145788.24 159572.04999999996 2024-10-13 31122 66930.23 66930.23 66930.23 66930.23 66930.23 66930.23 66930.23 66930.23 66930.23 66930.23 39280.229999999996 39280.229999999996 39280.229999999996 37381.229999999996 37381.229999999996 37381.229999999996 36431.729999999996 36431.729999999996 36431.729999999996 36431.729999999996 34541.729999999996 32608.059999999998 32608.059999999998 32608.059999999998 32608.059999999998 31391.559999999998 31391.559999999998 28629.89 28629.89 28629.89 27743.89 27743.89 27743.89 26712.64 26712.64 26712.64 26712.64 26712.64 24044.64 24044.64 24044.64 24044.64 24044.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 21824.64 20427.31 20427.31 20427.31 19097.31 19097.31 19097.31 18019.010000000002 18019.010000000002 18019.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 17869.010000000002 2024 4 10 41 287 3 2 13 2 13 0 0 0 0 0 0 0 1 157344.37000000002 63785.10999999999 59540.01 124406.49999999999 2024-10-14 31122 48571.93 48571.93 48571.93 48571.93 48571.93 48571.93 48571.93 48571.93 48571.93 48571.93 48571.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 14171.93 11410.26 11410.26 11410.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 10524.26 1052